In [1]:
import numpy as np
from scipy.linalg import sqrtm, logm
import mne

class GenerateurDonnees:
    def __init__(self, channels=3, sfreq=256.0, duration=10, change=5.0, A1=2.0e-6, A2=0.0e-6, sd=2.0e-6):
        self.channels = channels
        self.sfreq = sfreq
        self.duration = duration
        self.change = change
        self.frequencies = 10.0 + 2.0 * np.random.rand(channels)
        self.phases = 2.0 * np.pi * np.random.rand(channels)
        self.A1 = A1
        self.A2 = A2
        self.sd = sd
        self.info = mne.create_info([f'EEG{n:03}' for n in range(1, channels + 1)],
                                    ch_types=['eeg'] * channels, sfreq=sfreq)

    def generer_donnees(self):
        samples = int(self.sfreq * self.duration)
        t = np.linspace(0, self.duration, samples, endpoint=False)
        A = self.A1 + (t > self.change).astype(float) * (self.A2 - self.A1)
        data = A * np.cos(np.outer(self.frequencies, t) + np.outer(self.phases, np.ones(samples)))
        data += np.random.normal(0, self.sd, size=(self.channels, samples))
        # Vérification des valeurs infinies ou NaN
        if not np.isfinite(data).all():
            raise ValueError("Les données générées contiennent des valeurs infinies ou NaN")
        raw = mne.io.RawArray(data, self.info)
        return raw

    def exporter_donnees(self, filename='dummy.edf'):
        raw = self.generer_donnees()
        mne.export.export_raw(filename, raw, fmt='edf', overwrite=True)

In [2]:
import numpy as np

class CovarianceCalculator:
    def __init__(self, X, l, s):
        """
        Initialiser avec les données X, la longueur des segments l, et le décalage s.
        X : numpy array où les lignes sont les variables et les colonnes sont les échantillons.
        """
        self.X = X
        self.l = l
        self.s = s
        self.C = []
        self.calculate_covariance_matrices()
    
    def calculate_covariance_matrices(self):
        """
        Calculer les matrices de covariance successives à partir des données initiales.
        """
        m = self.X.shape[1]  # nombre de colonnes (échantillons)
        n = (m - self.l) // self.s + 1
        
        for k in range(n):
            start_idx = k * self.s
            end_idx = start_idx + self.l
            segment = self.X[:, start_idx:end_idx]
            cov_matrix = np.cov(segment)
            self.C.append(cov_matrix)
    
    def add_new_data(self, new_X):
        """
        Ajouter de nouvelles matrices de covariance à partir de nouvelles données.
        new_X : numpy array où les lignes sont les variables et les colonnes sont les échantillons.
        """
        m = new_X.shape[1]  # nombre de colonnes (échantillons)
        n = (m - self.l) // self.s + 1
        
        for k in range(n):
            start_idx = k * self.s
            end_idx = start_idx + self.l
            segment = new_X[:, start_idx:end_idx]
            cov_matrix = np.cov(segment)
            self.C.append(cov_matrix)


In [3]:
from scipy.linalg import sqrtm, logm

class Transformation:
    def __init__(self):
        pass

    def project_to_tangent(self, cov_matrix_current, cov_matrix_next):
        sqrt_B = sqrtm(cov_matrix_next)
        sqrt_inv_B = np.linalg.inv(sqrt_B)
        transformed_A = np.dot(np.dot(sqrt_inv_B, cov_matrix_current), sqrt_inv_B)
        log_transformed_A = logm(transformed_A)
        return log_transformed_A

    def transport_to_tangent(self, delta_matrix, tangent_plane_start, tangent_plane_end):
        inv_B = np.linalg.inv(tangent_plane_end)
        A_invB = np.dot(tangent_plane_start, inv_B)
        E = sqrtm(A_invB)
        transported_Delta = np.dot(np.dot(E, delta_matrix), E.T)
        return transported_Delta


In [4]:
class Trajectory:
    def __init__(self, covariance_matrices):
        """
        Initialiser avec une liste de matrices de covariance.
        """
        self.C = covariance_matrices
        self.transformation = Transformation()
        self.Deltas = self.calculate_deltas()

    def calculate_deltas(self):
        """
        Calculer les incréments et les transports successifs pour reconstruire la trajectoire.
        """
        Deltas = {}
        n = len(self.C)
        
        # Calcul des projections directes
        for i in range(n - 1):
            Deltas[(i, i+1)] = self.transformation.project_to_tangent(self.C[i], self.C[i+1])

        # Calcul des transports successifs
        for i in range(n - 1):
            for j in range(i + 2, n):
                Deltas[(i, j)] = self.transformation.transport_to_tangent(Deltas[(i, j-1)], self.C[j-1], self.C[j])

        return Deltas

    def get_delta(self, i, j):
        """
        Obtenir l'incrément ∆i,j
        """
        return self.Deltas.get((i, j), None)


In [5]:
class AntiDevelopment:
    def __init__(self, covariance_matrices):
        """
        Initialiser avec une liste de matrices de covariance.
        """
        self.C = covariance_matrices
        self.transformation = Transformation()
        self.A = self.calculate_antidevelopment()

    def calculate_antidevelopment(self):
        """
        Calculer l'anti-développement de la suite des matrices SPD.
        """
        A = []
        n = len(self.C)
        
        if n > 0:
            # Initialiser A1
            delta_0_1 = self.transformation.project_to_tangent(self.C[0], self.C[1])
            A.append((self.C[0], [delta_0_1]))

            for i in range(1, n - 1):
                # Calcul de ∆i, i+1
                delta_i_i1 = self.transformation.project_to_tangent(self.C[i], self.C[i+1])
                
                # Transport des ∆ précédents
                deltas = []
                for j in range(i):
                    delta = self.transformation.transport_to_tangent(A[i-1][1][j], self.C[i-1], self.C[i])
                    deltas.append(delta)
                deltas.append(delta_i_i1)
                
                A.append((self.C[i], deltas))

        return A

    def get_antidevelopment(self, index):
        """
        Obtenir l'anti-développement An pour un index donné.
        """
        if 0 <= index < len(self.A):
            return self.A[index]
        else:
            return None


In [6]:
import numpy as np

class TrajectorySPD:
    def __init__(self, anti_development, stride, frequency):
        """
        Initialiser avec une liste de couples (Cn, deltas), le stride, et la fréquence d'échantillonnage.
        anti_development : liste de tuples (Cn, deltas)
        stride : décalage entre les segments
        frequency : fréquence d'échantillonnage en Hz
        """
        self.A = anti_development
        self.stride = stride
        self.frequency = frequency
        self.time_stamps = self.calculate_time_stamps()
        self.transformation = Transformation()
        self.T = self.calculate_trajectory()

    def calculate_time_stamps(self):
        """
        Calculer les instants d'échantillonnage.
        """
        n = len(self.A)
        t = np.arange(n) * (self.stride / self.frequency)
        return t

    def calculate_trajectory(self):
        """
        Calculer la trajectoire à partir de l'anti-développement et des instants d'échantillonnage.
        """
        T = {}
        k = len(self.A) - 1

        for j in range(k, 0, -1):
            time_diff = self.time_stamps[j] - self.time_stamps[j-1]
            delta_transported = self.transformation.transport_to_tangent(self.A[k][1][j-1], self.A[k][0], np.eye(self.A[k][0].shape[0]))
            T[j] = time_diff * delta_transported 
        
        for i in range(k-1, 0, -1):
            T[i] = T[i+1] + T[i]
        return T

    def get_trajectory(self, index):
        """
        Obtenir la trajectoire à l'index donné.
        """
        return self.T.get(index, None)


In [32]:
if __name__ == "__main__":
    # Exemple de données initiales
    generateur = GenerateurDonnees()
    X_raw = generateur.generer_donnees()
    X = X_raw.get_data()
    l = 20  # longueur des segments
    s = 10  # décalage entre les segments
    f = 256.0  # fréquence d'échantillonnage

    # Créer une instance de la classe et calculer les matrices de covariance
    calc = CovarianceCalculator(X, l, s)
    
    # Créer une instance de Trajectory pour calculer les trajectoires à partir des matrices de covariance
    traj = Trajectory(calc.C)
    
    # Afficher les deltas calculés
    #for key, delta in traj.Deltas.items():
    #    print(f"Delta {key}:")
    #    print(delta)

    # Créer une instance de AntiDevelopment pour calculer l'anti-développement
    anti_dev = AntiDevelopment(calc.C)
    # Afficher l'anti-développement calculé
    #for index, anti_dev_item in enumerate(anti_dev.A):
    #    print(f"Anti-développement A{index}:")
    #    print("Matrice de covariance:", anti_dev_item[0])
    #    print("Deltas:", anti_dev_item[1])
    
    # Créer une instance de TrajectorySPD pour calculer la trajectoire
    trajectory_spd = TrajectorySPD(anti_dev.A, s, f)
    
    # Afficher la trajectoire calculée
    for index, traj in trajectory_spd.T.items():
        print(f"Trajectoire T{index}:")
        print(traj)
    


Creating RawArray with float64 data, n_channels=3, n_times=2560
    Range : 0 ... 2559 =      0.000 ...     9.996 secs
Ready.
Trajectoire T253:
[[ 6.17682230e-14 -3.22966239e-14  2.52585411e-14]
 [-3.22966239e-14  6.95831982e-14 -4.24262471e-14]
 [ 2.52585411e-14 -4.24262471e-14 -2.12133234e-14]]
Trajectoire T252:
[[ 8.39071446e-14 -3.25191124e-14  3.23551782e-14]
 [-3.25191124e-14  8.68807018e-14 -7.30246236e-14]
 [ 3.23551782e-14 -7.30246236e-14  6.52464190e-15]]
Trajectoire T251:
[[ 4.05248915e-14 -3.33933684e-14  3.54194761e-14]
 [-3.33933684e-14  5.81597695e-14 -3.41427247e-14]
 [ 3.54194761e-14 -3.41427247e-14 -1.83584133e-14]]
Trajectoire T250:
[[ 1.63552886e-14 -1.72116543e-14  2.08131257e-14]
 [-1.72116543e-14  1.33984268e-13 -3.80080655e-14]
 [ 2.08131257e-14 -3.80080655e-14 -5.03944093e-15]]
Trajectoire T249:
[[ 6.99019675e-14 -6.09146616e-14 -5.35629900e-14]
 [-6.09146616e-14  2.24406449e-13 -1.79269937e-14]
 [-5.35629900e-14 -1.79269937e-14  6.29327403e-14]]
Trajectoire T2

In [9]:
import mne
import moabb
import numpy as np
from moabb.datasets import BNCI2014_001

In [31]:
dataset = BNCI2014_001()
sessions = dataset.get_data(subjects=[1])
subject = 1
session_name = "0train"
run_name = "0"
raw = sessions[subject][session_name][run_name]
raw=raw.pick_types(eeg=True,exclude='bads')

NOTE: pick_types() is a legacy function. New code should use inst.pick(...).


In [ ]:
raw.info

<Info | 8 non-empty values
 bads: []
 ch_names: Fz, FC3, FC1, FCz, FC2, FC4, C5, C3, C1, Cz, C2, C4, C6, CP3, ...
 chs: 22 EEG
 custom_ref_applied: False
 dig: 25 items (3 Cardinal, 22 EEG)
 highpass: 0.0 Hz
 lowpass: 125.0 Hz
 meas_date: unspecified
 nchan: 22
 projs: []
 sfreq: 250.0 Hz
>

In [33]:
import numpy as np

def is_positive_definite(matrix):
    eigvals = np.linalg.eigvals(matrix)
    return np.all(eigvals > 0)

# Exemple d'utilisation
A = calc.C[0]
print(is_positive_definite(A))  # True

True


In [ ]:
import numpy as np

def is_positive_definite(matrix):
    eigvals = np.linalg.eigvals(matrix)
    return np.all(eigvals > 0)

for i in range(0, len(calc.C)):
    A = calc.C[i]
    print(is_positive_definite(A))  # True


In [ ]:
import numpy as np

def is_positive_definite(matrix):
    eigvals = np.linalg.eigvals(matrix)
    return np.all(eigvals > 0)

for i in range(0, len(anti_dev.A)):
    A = anti_dev.A[i][1][-1]
    print(is_positive_definite(A))  # True


In [36]:
if __name__ == "__main__":
    
    X = raw.get_data()
    l = 256  # longueur des segments
    s = 128  # décalage entre les segments
    f = 256.0  # fréquence d'échantillonnage

    # Créer une instance de la classe et calculer les matrices de covariance
    calc = CovarianceCalculator(X, l, s)
    
    # Créer une instance de Trajectory pour calculer les trajectoires à partir des matrices de covariance
    traj = Trajectory(calc.C)
    
    # Afficher les deltas calculés
    #for key, delta in traj.Deltas.items():
    #    print(f"Delta {key}:")
    #    print(delta)

    # Créer une instance de AntiDevelopment pour calculer l'anti-développement
    anti_dev = AntiDevelopment(calc.C)
    # Afficher l'anti-développement calculé
    #for index, anti_dev_item in enumerate(anti_dev.A):
    #    print(f"Anti-développement A{index}:")
    #    print("Matrice de covariance:", anti_dev_item[0])
    #    print("Deltas:", anti_dev_item[1])
    
    # Créer une instance de TrajectorySPD pour calculer la trajectoire
    trajectory_spd = TrajectorySPD(anti_dev.A, s, f)
    
    # Afficher la trajectoire calculée
    for index, traj in trajectory_spd.T.items():
        print(f"Trajectoire T{index}:")
        print(traj)
    


Trajectoire T752:
[[9.90022499e-07 7.55859913e-07 7.58769477e-07 7.90316068e-07
  7.75102145e-07 7.94646292e-07 5.13964199e-07 5.97779671e-07
  6.47352874e-07 6.53701706e-07 6.74028288e-07 6.39839242e-07
  5.75963325e-07 5.05102536e-07 5.63461242e-07 5.74273114e-07
  5.79945995e-07 5.42375637e-07 4.40413636e-07 4.63046685e-07
  4.49562940e-07 3.17691690e-07]
 [7.55859913e-07 5.77163497e-07 5.79372041e-07 6.03448551e-07
  5.91826415e-07 6.06729451e-07 3.92518021e-07 4.56541130e-07
  4.94383164e-07 4.99232827e-07 5.14726782e-07 4.88622456e-07
  4.39808839e-07 3.85853949e-07 4.30406345e-07 4.38670580e-07
  4.42974659e-07 4.14273896e-07 3.36510730e-07 3.53787484e-07
  3.43467676e-07 2.42804615e-07]
 [7.58769477e-07 5.79372041e-07 5.81593620e-07 6.05766464e-07
  5.94103634e-07 6.09069027e-07 3.94008965e-07 4.58277654e-07
  4.96270440e-07 5.01142472e-07 5.16703280e-07 4.90502425e-07
  4.41506109e-07 3.87309032e-07 4.32038613e-07 4.40338038e-07
  4.44667489e-07 4.15862035e-07 3.37772876e-07 3